In [0]:
dim_rider = spark.sql('''
select rider_id, first_name, last_name, address, birthday, start_date, end_date, is_member from riders''')

dim_rider.dropDuplicates(["rider_id"]).write.format("delta").mode("overwrite").saveAsTable("dim_rider")

In [0]:
dim_station = spark.sql('''
select station_id, name, latitude, longtitude from stations''')

dim_station.dropDuplicates(["station_id"]).write.format("delta").mode("overwrite").saveAsTable("dim_station")

In [0]:
from pyspark.sql import functions as f
from pyspark.sql.types import StringType

min_date_query = spark.sql('''select MIN(started_at) as started_at from trips''')
min_date = min_date_query.first().asDict()['started_at']

max_date_query = spark.sql('''select DATEADD(year, 5, MAX(started_at)) as started_at from trips''')
max_date = max_date_query.first().asDict()['started_at']

expression = f"sequence(to_date('{min_date}'), to_date('{max_date}'), interval 1 day)"

In [0]:
dim_time = spark.createDataFrame([(1,)], ["time_id"])

dim_time = dim_time.withColumn("dateinit", f.explode(f.expr(expression)))
dim_time = dim_time.withColumn("date", f.to_timestamp(dim_time.dateinit, "yyyy-MM-dd"))
dim_time = dim_time \
            .withColumn("dayofweek", f.dayofweek(dim_time.date)) \
            .withColumn("dayofmonth", f.dayofmonth(dim_time.date)) \
            .withColumn("weekofyear", f.weekofyear(dim_time.date)) \
            .withColumn("year", f.year(dim_time.date)) \
            .withColumn("quarter", f.quarter(dim_time.date)) \
            .withColumn("month", f.month(dim_time.date)) \
            .withColumn("time_id", dim_time.date.cast(StringType())) \
            .drop(f.col("dateinit"))
                  
display(dim_time)

time_id date dayofweek dayofmonth weekofyear year quarter month 2021-02-01 00:00:00 2021-02-01T00:00:00.000+0000 2 1 5 2021 1 2 2021-02-02 00:00:00 2021-02-02T00:00:00.000+0000 3 2 5 2021 1 2 2021-02-03 00:00:00 2021-02-03T00:00:00.000+0000 4 3 5 2021 1 2 2021-02-04 00:00:00 2021-02-04T00:00:00.000+0000 5 4 5 2021 1 2 2021-02-05 00:00:00 2021-02-05T00:00:00.000+0000 6 5 5 2021 1 2 2021-02-06 00:00:00 2021-02-06T00:00:00.000+0000 7 6 5 2021 1 2 2021-02-07 00:00:00 2021-02-07T00:00:00.000+0000 1 7 5 2021 1 2 2021-02-08 00:00:00 2021-02-08T00:00:00.000+0000 2 8 6 2021 1 2 2021-02-09 00:00:00 2021-02-09T00:00:00.000+0000 3 9 6 2021 1 2 2021-02-10 00:00:00 2021-02-10T00:00:00.000+0000 4 10 6 2021 1 2 2021-02-11 00:00:00 2021-02-11T00:00:00.000+0000 5 11 6 2021 1 2 2021-02-12 00:00:00 2021-02-12T00:00:00.000+0000 6 12 6 2021 1 2 2021-02-13 00:00:00 2021-02-13T00:00:00.000+0000 7 13 6 2021 1 2 2021-02-14 00:00:00 2021-02-14T00:00:00.000+0000 1 14 6 2021 1 2 2021-02-15 00:00:00 2021-02-15T00:00:00.000+0000 2 15 7 2021 1 2 2021-02-16 00:00:00 2021-02-16T00:00:00.000+0000 3 16 7 2021 1 2 2021-02-17 00:00:00 2021-02-17T00:00:00.000+0000 4 17 7 2021 1 2 2021-02-18 00:00:00 2021-02-18T00:00:00.000+0000 5 18 7 2021 1 2 2021-02-19 00:00:00 2021-02-19T00:00:00.000+0000 6 19 7 2021 1 2 2021-02-20 00:00:00 2021-02-20T00:00:00.000+0000 7 20 7 2021 1 2 2021-02-21 00:00:00 2021-02-21T00:00:00.000+0000 1 21 7 2021 1 2 2021-02-22 00:00:00 2021-02-22T00:00:00.000+0000 2 22 8 2021 1 2 2021-02-23 00:00:00 2021-02-23T00:00:00.000+0000 3 23 8 2021 1 2 2021-02-24 00:00:00 2021-02-24T00:00:00.000+0000 4 24 8 2021 1 2 2021-02-25 00:00:00 2021-02-25T00:00:00.000+0000 5 25 8 2021 1 2 2021-02-26 00:00:00 2021-02-26T00:00:00.000+0000 6 26 8 2021 1 2 2021-02-27 00:00:00 2021-02-27T00:00:00.000+0000 7 27 8 2021 1 2 2021-02-28 00:00:00 2021-02-28T00:00:00.000+0000 1 28 8 2021 1 2 2021-03-01 00:00:00 2021-03-01T00:00:00.000+0000 2 1 9 2021 1 3 2021-03-02 00:00:00 2021-03-02T00:00:00.000+0000 3 2 9 2021 1 3 2021-03-03 00:00:00 2021-03-03T00:00:00.000+0000 4 3 9 2021 1 3 2021-03-04 00:00:00 2021-03-04T00:00:00.000+0000 5 4 9 2021 1 3 2021-03-05 00:00:00 2021-03-05T00:00:00.000+0000 6 5 9 2021 1 3 2021-03-06 00:00:00 2021-03-06T00:00:00.000+0000 7 6 9 2021 1 3 2021-03-07 00:00:00 2021-03-07T00:00:00.000+0000 1 7 9 2021 1 3 2021-03-08 00:00:00 2021-03-08T00:00:00.000+0000 2 8 10 2021 1 3 2021-03-09 00:00:00 2021-03-09T00:00:00.000+0000 3 9 10 2021 1 3 2021-03-10 00:00:00 2021-03-10T00:00:00.000+0000 4 10 10 2021 1 3 2021-03-11 00:00:00 2021-03-11T00:00:00.000+0000 5 11 10 2021 1 3 2021-03-12 00:00:00 2021-03-12T00:00:00.000+0000 6 12 10 2021 1 3 2021-03-13 00:00:00 2021-03-13T00:00:00.000+0000 7 13 10 2021 1 3 2021-03-14 00:00:00 2021-03-14T00:00:00.000+0000 1 14 10 2021 1 3 2021-03-15 00:00:00 2021-03-15T00:00:00.000+0000 2 15 11 2021 1 3 2021-03-16 00:00:00 2021-03-16T00:00:00.000+0000 3 16 11 2021 1 3 2021-03-17 00:00:00 2021-03-17T00:00:00.000+0000 4 17 11 2021 1 3 2021-03-18 00:00:00 2021-03-18T00:00:00.000+0000 5 18 11 2021 1 3 2021-03-19 00:00:00 2021-03-19T00:00:00.000+0000 6 19 11 2021 1 3 2021-03-20 00:00:00 2021-03-20T00:00:00.000+0000 7 20 11 2021 1 3 2021-03-21 00:00:00 2021-03-21T00:00:00.000+0000 1 21 11 2021 1 3 2021-03-22 00:00:00 2021-03-22T00:00:00.000+0000 2 22 12 2021 1 3 2021-03-23 00:00:00 2021-03-23T00:00:00.000+0000 3 23 12 2021 1 3 2021-03-24 00:00:00 2021-03-24T00:00:00.000+0000 4 24 12 2021 1 3 2021-03-25 00:00:00 2021-03-25T00:00:00.000+0000 5 25 12 2021 1 3 2021-03-26 00:00:00 2021-03-26T00:00:00.000+0000 6 26 12 2021 1 3 2021-03-27 00:00:00 2021-03-27T00:00:00.000+0000 7 27 12 2021 1 3 2021-03-28 00:00:00 2021-03-28T00:00:00.000+0000 1 28 12 2021 1 3 2021-03-29 00:00:00 2021-03-29T00:00:00.000+0000 2 29 13 2021 1 3 2021-03-30 00:00:00 2021-03-30T00:00:00.000+0000 3 30 13 2021 1 3 2021-03-31 00:00:00 2021-03-31T00:00:00.000+0000 4 31 13 2021 1 3 2021-04-01 00:00:00 2021-04-01T00:00:00.000+0000 5 1 13 2021 2 4 2021-04-02 00:00:00 2021-04-02

In [0]:
dim_time.write \
.format("delta") \
.mode("overwrite") \
.saveAsTable("dim_time")

In [0]:
#from pyspark.sql.functions import col
trips = spark.sql('''select * from trips''')

fact_trip = spark.sql('''
    SELECT 
        trips.trip_id,
        riders.rider_id,
        trips.start_station_id, 
        trips.end_station_id, 
        trips.rideable_type, 
        trips.started_at, 
        trips.ended_at, 
        DATEDIFF(hour, trips.started_at, trips.ended_at) AS duration,
        DATEDIFF(year, riders.birthday, trips.started_at) AS rider_age
    FROM trips JOIN riders ON riders.rider_id = trips.rider_id
''')
display(fact_trip)

trip_id rider_id start_station_id end_station_id rideable_type started_at ended_at duration rider_age 222BB8E5059252D7 34062 KA1503000064 13021 classic_bike 2021-06-13 09:48:47 2021-06-13 10:07:23 0 30 1826E16CB5486018 5342 TA1306000010 13021 classic_bike 2021-06-21 22:59:13 2021-06-21 23:04:29 0 26 3D9B6A0A5330B04D 3714 TA1305000030 13021 classic_bike 2021-06-18 16:06:42 2021-06-18 16:12:02 0 26 07E82F5E9C9E490F 18793 TA1305000034 13021 classic_bike 2021-06-17 16:46:23 2021-06-17 17:02:45 0 18 A8E94BAECBF0C2DD 43342 TA1308000009 TA1308000009 docked_bike 2021-06-13 17:36:29 2021-06-13 18:30:39 0 28 378F4AB323AA1D14 6693 TA1308000009 TA1308000009 docked_bike 2021-06-13 13:20:10 2021-06-13 14:06:14 0 28 38AD311DC2EB1FBE 71480 KA1503000019 KA1503000019 docked_bike 2021-06-16 17:14:30 2021-06-16 17:28:34 0 56 1D466737F0B18097 50846 TA1308000009 TA1308000009 docked_bike 2021-06-27 14:51:52 2021-06-27 15:26:39 0 40 27E1142E1ACFAEFB 18951 13257 13257 electric_bike 2021-06-21 13:58:26 2021-06-21 13:58:53 0 21 67F2A115DAE77924 63987 TA1308000009 TA1308000009 classic_bike 2021-06-22 00:51:43 2021-06-22 01:08:25 0 37 D30A0F588CAB9948 52600 13036 13434 docked_bike 2021-06-03 16:40:02 2021-06-03 17:04:22 0 39 B6D051538810CE8A 58393 KA1503000064 TA1308000009 classic_bike 2021-06-14 19:19:04 2021-06-14 19:55:54 0 21 9724F787201C914E 45636 13042 13434 classic_bike 2021-06-06 19:37:03 2021-06-06 19:56:22 0 28 5C07EC15B5E1F93C 66194 13084 13257 classic_bike 2021-06-19 20:17:01 2021-06-19 20:27:19 0 30 1BFBE159F63DF1AF 18576 KA1503000043 13021 classic_bike 2021-06-30 09:06:25 2021-06-30 09:09:11 0 32 C63897EB5765B1E6 62971 TA1306000003 13021 classic_bike 2021-06-11 22:46:36 2021-06-11 22:49:03 0 39 AAA3B86E0B459EBB 8235 KA1503000043 13434 electric_bike 2021-06-10 15:56:15 2021-06-10 16:03:51 0 33 B22FA59E25D85FFB 51431 13157 13021 electric_bike 2021-06-10 17:20:02 2021-06-10 17:26:05 0 46 ADA725E548D6CF84 40507 KA1503000043 13434 electric_bike 2021-06-08 16:12:24 2021-06-08 16:19:32 0 36 AC061F7C81D386EE 67393 13016 13021 electric_bike 2021-06-25 10:04:56 2021-06-25 10:15:01 0 24 92AFE274FABD11CE 16460 KA17018054 13021 classic_bike 2021-06-05 12:01:26 2021-06-05 12:17:16 0 18 3256D982124A51CC 75162 657 13257 classic_bike 2021-06-04 19:00:27 2021-06-04 19:12:47 0 24 F863618B48098D75 13478 13059 13021 docked_bike 2021-06-03 01:16:01 2021-06-05 18:07:36 64 34 71DE5B8A7F699133 62165 TA1307000164 TA1308000009 classic_bike 2021-06-11 20:58:10 2021-06-11 21:10:53 0 48 F27720C77BF53D45 72120 TA1309000033 13257 classic_bike 2021-06-02 19:00:27 2021-06-02 19:18:29 0 24 70450A18BC3E1D2C 40507 KA1503000043 13434 electric_bike 2021-06-26 23:05:28 2021-06-26 23:20:08 0 36 67D4F59EF1AF0860 38429 KA1503000043 13434 electric_bike 2021-06-14 15:39:18 2021-06-14 15:46:29 0 38 E3C9A476285BCAC6 32429 13042 TA1308000009 classic_bike 2021-06-27 12:18:43 2021-06-27 14:15:43 1 20 FD52122A0097A531 65021 WL-012 13021 classic_bike 2021-06-01 16:37:20 2021-06-01 16:39:29 0 58 62488E6B93B305DC 42347 WL-012 13021 classic_bike 2021-06-18 19:52:27 2021-06-18 20:51:45 0 21 C2B3554CF7143205 22598 TA1309000029 13257 classic_bike 2021-06-19 02:05:11 2021-06-19 02:14:15 0 27 65DF68F8CFF425AC 54690 TA1307000128 13257 classic_bike 2021-06-09 18:30:03 2021-06-09 19:07:43 0 22 0FB0BE3484716E54 13575 TA1305000022 13021 classic_bike 2021-06-08 22:50:01 2021-06-08 22:55:21 0 38 695E965A2C32C219 21558 518 13257 electric_bike 2021-06-20 15:32:28 2021-06-20 15:53:48 0 51 CC5F8FDFD92095F0 65266 KA1504000135 13257 electric_bike 2021-06-08 13:09:35 2021-06-08 13:30:14 0 42 6D860D9BBE025B69 48144 KA1504000135 13021 classic_bike 2021-06-18 16:46:00 2021-06-18 16:57:01 0 35 F7B56023FD693D70 49504 TA1307000128 13021 electric_bike 2021-06-01 13:34:50 2021-06-01 13:45:24 0 20 255C4D03ABFE2986 20626 657 13021 electric_bike 2021-06-21 08:46:32 2021-06-21 08:58:42 0 23 8196B8C3543C9B67 66950 518 13257 classic_bike 2021-06-12 11:22:07 2021-06-12 11:42:57 0 46 E75063B987852D07 56559 TA1307000163 13257 clas

In [0]:
fact_trip.write \
.format("delta") \
.mode("overwrite") \
.saveAsTable("fact_trip")

In [0]:
fact_payment = spark.sql('''
    SELECT
        payment_id,
        payments.amount,
        payments.rider_id,
        dim_time.time_id
    FROM payments
    JOIN dim_time ON dim_time.date = payments.date
''')

display(fact_payment)

payment_id amount rider_id time_id 22 9.0 1000 2021-02-01 00:00:00 23 9.0 1000 2021-03-01 00:00:00 24 9.0 1000 2021-04-01 00:00:00 25 9.0 1000 2021-05-01 00:00:00 26 9.0 1000 2021-06-01 00:00:00 27 9.0 1000 2021-07-01 00:00:00 28 9.0 1000 2021-08-01 00:00:00 29 9.0 1000 2021-09-01 00:00:00 30 9.0 1000 2021-10-01 00:00:00 31 9.0 1000 2021-11-01 00:00:00 32 9.0 1000 2021-12-01 00:00:00 33 9.0 1000 2022-01-01 00:00:00 34 9.0 1000 2022-02-01 00:00:00 62 6.56 1003 2021-02-01 00:00:00 63 7.4 1003 2021-03-01 00:00:00 64 18.31 1003 2021-04-01 00:00:00 65 14.48 1003 2021-05-01 00:00:00 66 6.5 1003 2021-06-01 00:00:00 67 12.35 1003 2021-07-01 00:00:00 68 22.84 1003 2021-08-01 00:00:00 69 20.45 1003 2021-09-01 00:00:00 70 5.24 1003 2021-10-01 00:00:00 71 14.16 1003 2021-11-01 00:00:00 72 13.06 1003 2021-12-01 00:00:00 73 14.28 1003 2022-01-01 00:00:00 74 18.61 1003 2022-02-01 00:00:00 91 9.0 1004 2021-02-01 00:00:00 92 9.0 1004 2021-03-01 00:00:00 93 9.0 1004 2021-04-01 00:00:00 94 9.0 1004 2021-05-01 00:00:00 95 9.0 1004 2021-06-01 00:00:00 96 9.0 1004 2021-07-01 00:00:00 97 9.0 1004 2021-08-01 00:00:00 98 9.0 1004 2021-09-01 00:00:00 99 9.0 1004 2021-10-01 00:00:00 100 9.0 1004 2021-11-01 00:00:00 101 9.0 1004 2021-12-01 00:00:00 102 9.0 1004 2022-01-01 00:00:00 103 9.0 1004 2022-02-01 00:00:00 114 3.62 1005 2021-02-01 00:00:00 115 9.46 1005 2021-03-01 00:00:00 116 11.44 1005 2021-04-01 00:00:00 117 6.73 1005 2021-05-01 00:00:00 118 24.28 1005 2021-06-01 00:00:00 119 19.36 1005 2021-07-01 00:00:00 120 20.49 1005 2021-08-01 00:00:00 121 18.24 1005 2021-09-01 00:00:00 122 3.27 1005 2021-10-01 00:00:00 123 18.39 1005 2021-11-01 00:00:00 124 11.24 1005 2021-12-01 00:00:00 125 3.9 1005 2022-01-01 00:00:00 126 22.17 1005 2022-02-01 00:00:00 129 9.0 1006 2021-02-01 00:00:00 130 9.0 1006 2021-03-01 00:00:00 131 9.0 1006 2021-04-01 00:00:00 132 9.0 1006 2021-05-01 00:00:00 133 9.0 1006 2021-06-01 00:00:00 134 9.0 1006 2021-07-01 00:00:00 135 9.0 1006 2021-08-01 00:00:00 136 9.0 1006 2021-09-01 00:00:00 137 9.0 1006 2021-10-01 00:00:00 138 9.0 1006 2021-11-01 00:00:00 139 9.0 1006 2021-12-01 00:00:00 189 4.05 1007 2021-02-01 00:00:00 190 9.07 1007 2021-03-01 00:00:00 191 21.46 1007 2021-04-01 00:00:00 192 19.45 1007 2021-05-01 00:00:00 193 4.29 1007 2021-06-01 00:00:00 194 10.76 1007 2021-07-01 00:00:00 195 24.51 1007 2021-08-01 00:00:00 196 5.03 1007 2021-09-01 00:00:00 197 24.08 1007 2021-10-01 00:00:00 198 9.2 1007 2021-11-01 00:00:00 199 20.5 1007 2021-12-01 00:00:00 200 4.58 1007 2022-01-01 00:00:00 201 23.48 1007 2022-02-01 00:00:00 202 9.0 1008 2021-04-01 00:00:00 203 9.0 1008 2021-05-01 00:00:00 204 9.0 1008 2021-06-01 00:00:00 205 9.0 1008 2021-07-01 00:00:00 213 9.0 1009 2021-02-01 00:00:00 214 9.0 1009 2021-03-01 00:00:00 215 9.0 1009 2021-04-01 00:00:00 216 9.0 1009 2021-05-01 00:00:00 217 9.0 1009 2021-06-01 00:00:00 218 9.0 1009 2021-07-01 00:00:00 219 9.0 1009 2021-08-01 00:00:00 220 9.0 1009 2021-09-01 00:00:00 221 9.0 1009 2021-10-01 00:00:00 222 9.0 1009 2021-11-01 00:00:00 236 9.0 1010 2021-02-01 00:00:00 237 9.0 1010 2021-03-01 00:00:00 238 9.0 1010 2021-04-01 00:00:00 239 9.0 1010 2021-05-01 00:00:00 240 9.0 1010 2021-06-01 00:00:00 241 9.0 1010 2021-07-01 00:00:00 242 9.0 1010 2021-08-01 00:00:00 243 9.0 1010 2021-09-01 00:00:00 244 9.0 1010 2021-10-01 00:00:00 245 9.0 1010 2021-11-01 00:00:00 246 9.0 1010 2021-12-01 00:00:00 247 9.0 1010 2022-01-01 00:00:00 248 9.0 1010 2022-02-01 00:00:00 293 9.0 1011 2021-02-01 00:00:00 294 9.0 1011 2021-03-01 00:00:00 295 9.0 1011 2021-04-01 00:00:00 296 9.0 1011 2021-05-01 00:00:00 297 9.0 1011 2021-06-01 00:00:00 298 9.0 1011 2021-07-01 00:00:00 299 9.0 1011 2021-08-01 00:00:00 300 9.0 1011 2021-09-01 00:00:00 301 9.0 1011 2021-10-01 00:00:00 302 9.0 1011 2021-11-01 00:00:00 303 9.0 1011 2021-12-01 00:00:00 304 9.0 1011 2022-01-01 00:00:00 305 9.0 1011 2022-02-01 00:00:00 306 9.0 1012 2021-11-01 00:00:00 307 9.0 1012 2021-12-01 00:00:00 308 9.0 1012 2022-01-01 00:00:00 309 9.0 1012 20

In [0]:
fact_payment.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("fact_payment")